In [1]:
import geopandas as gpd
shapefile = 'geopandas/ne_110m_admin_0_countries.shp'
#Read shapefile using Geopandas
gdf = gpd.read_file(shapefile)[['ADMIN', 'ADM0_A3', 'geometry']]
#Rename columns.
gdf.columns = ['country', 'country_code', 'geometry']
gdf.to_csv('country_geo.csv', index=False)
gdf

country country_code  \
0                           Fiji          FJI   
1    United Republic of Tanzania          TZA   
2                 Western Sahara          SAH   
3                         Canada          CAN   
4       United States of America          USA   
..                           ...          ...   
172           Republic of Serbia          SRB   
173                   Montenegro          MNE   
174                       Kosovo          KOS   
175          Trinidad and Tobago          TTO   
176                  South Sudan          SDS   

                                              geometry  
0    MULTIPOLYGON (((180.00000 -16.06713, 180.00000...  
1    POLYGON ((33.90371 -0.95000, 34.07262 -1.05982...  
2    POLYGON ((-8.66559 27.65643, -8.66512 27.58948...  
3    MULTIPOLYGON (((-122.84000 49.00000, -122.9742...  
4    MULTIPOLYGON (((-122.84000 49.00000, -120.0000...  
..                                                 ...  
172  POLYGON ((18.82982 45.90887, 18.82984 45.90888...  
173  POLYGON ((20.07070 42.58863, 19.80161 42.50009...  
174  POLYGON ((20.59025 41.85541, 20.52295 42.21787...  
175  POLYGON ((-61.68000 10.76000, -61.10500 10.890...  
176  POLYGON ((30.83385 3.50917, 29.95350 4.17370, ...  

[177 rows x 3 columns]

In [2]:
from bokeh.io import curdoc, output_notebook, show
from bokeh.models import HoverTool, GeoJSONDataSource, LinearColorMapper, ColorBar, LabelSet
from bokeh.layouts import widgetbox, row, column
from bokeh.palettes import Blues8
from bokeh.plotting import figure, ColumnDataSource
output_notebook()

Loading BokehJS ...

In [3]:
import json
with open("country_geo.json") as f:
    data = json.load(f)
json_data = json.dumps(data)

In [4]:
geosource = GeoJSONDataSource(geojson = json_data)

palette = Blues8
palette = palette[::-1]
color_mapper = LinearColorMapper(palette = palette, low = 0, high = 8, nan_color = '#d9d9d9')
tick_labels = {'0':'1', '1': '10', '2': '50', '3':'100', '4':'500', '5':'1000', '6':'5000', '7':'10000', '8':''}

color_bar = ColorBar(color_mapper=color_mapper, label_standoff=12, width = 20, height = 320, scale_alpha=0.6,
                     border_line_color=None, location = (0,0), orientation = 'vertical', major_label_overrides = tick_labels)

p = figure(title = 'country patents count', plot_height = 500 , plot_width = 1000, 
           tools = 'pan,wheel_zoom,save,reset', toolbar_location='above')
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None

p.patches('xs','ys', source = geosource, fill_color = {'field' :'class', 'transform' : color_mapper},
          line_color = '#192841', line_alpha=0.7, line_width = 0.15, fill_alpha = 0.6)

hover = HoverTool()
hover.tooltips = [('Country / Region','@country'),('Patents Count', '@count')]
p.add_tools(hover)

p.add_layout(color_bar, 'right')

show(p)

In [5]:
import pandas as pd
df = pd.read_csv('country_geo_count.csv')

In [6]:
df = df.sort_values('count', ascending=False)
df2 = df.head(10).sort_values('count', ascending=True)

In [7]:
factors = df2['country'].tolist()
x = df2['count'].tolist()
source2 = ColumnDataSource(df2)

dot = figure(title="top10 country ranking", tools='pan,wheel_zoom,save,reset', toolbar_location='above',
            y_range=factors, x_range=[0,62500], plot_height = 400 , plot_width = 600)
dot.ygrid.grid_line_color = None

dot.segment(0, 'country', 'count', 'country', line_width=2, line_color="#7f7f7f", line_alpha=0.6, source=source2)
c = dot.circle(x='count', y='country', size=12, fill_color="#588BAE", fill_alpha=1, line_color="#588BAE", line_width=2, source=source2)

from bokeh.models import GlyphRenderer, Circle
grs = c.select(dict(type=GlyphRenderer))
for glyph in grs:
    if isinstance(glyph.glyph, Circle):
        circle_renderer = glyph

hover = HoverTool(renderers = [circle_renderer], mode='hline')
hover.tooltips = [('Country / Region','@country'),('Patents Count', '@count')]
dot.add_tools(hover)

graphs = row(dot, p)
show(graphs)